# 🔍 CUIDAR IA - Exploración del Sistema RAG

**Objetivo:** Probar y validar el sistema RAG (Retrieval-Augmented Generation) con documentos científicos sobre prevención del suicidio.

**Fase:** 2 - RAG Development

**Documentos de prueba:**
1. Clinical Pathway for Suicide Risk Screening (Enfoques Clínicos)
2. Ethics and Governance of AI for Health - OMS (Fundamentos Éticos)
3. Effectiveness of suicide prevention interventions (Salud Pública)

---

## 1️⃣ Setup y Configuración

Importar librerías y cargar variables de entorno.

In [19]:
# Importar librerías base
import os
import sys
from pathlib import Path
from dotenv import load_dotenv
import warnings
warnings.filterwarnings('ignore')

# Cargar variables de entorno
project_root = Path.cwd().parent.parent
env_path = project_root / '.env'
load_dotenv(env_path)

print("✅ Variables de entorno cargadas")
print(f"📁 Ruta del proyecto: {project_root}")
print(f"🔑 API Key configurada: {'Sí' if os.getenv('OPENAI_API_KEY') else 'No'}")

✅ Variables de entorno cargadas
📁 Ruta del proyecto: /Users/reinerfuentesferrada/ONLINE_DS_THEBRIDGE_Rei/Proyecto ML/cuidar-ia
🔑 API Key configurada: Sí


In [20]:
# Importar librerías para RAG
from openai import OpenAI
from pypdf import PdfReader
import tiktoken
from langchain_text_splitters import RecursiveCharacterTextSplitter
from langchain_openai import OpenAIEmbeddings
from langchain_community.vectorstores import Chroma
from langchain_core.documents import Document
import json
from datetime import datetime

print("✅ Librerías RAG importadas correctamente")

✅ Librerías RAG importadas correctamente


---
## 2️⃣ Test de Conexión con OpenAI

Verificar que la API key funciona correctamente antes de continuar.

In [21]:
# Inicializar cliente de OpenAI
client = OpenAI(api_key=os.getenv('OPENAI_API_KEY'))

# Test de conexión simple
try:
    response = client.chat.completions.create(
        model="gpt-4o-mini",
        messages=[
            {"role": "system", "content": "Eres un asistente experto en salud mental y prevención del suicidio."},
            {"role": "user", "content": "Di 'Conexión exitosa' si puedes leer este mensaje."}
        ],
        max_tokens=50
    )
    
    print("✅ CONEXIÓN EXITOSA con OpenAI API")
    print(f"📝 Respuesta: {response.choices[0].message.content}")
    print(f"💰 Tokens usados: {response.usage.total_tokens}")
    
except Exception as e:
    print(f"❌ ERROR en la conexión: {e}")
    print("Verifica tu API key en el archivo .env")

✅ CONEXIÓN EXITOSA con OpenAI API
📝 Respuesta: Conexión exitosa. Estoy aquí para ayudarte. ¿En qué puedo asistirte hoy?
💰 Tokens usados: 59


---
## 3️⃣ Carga de PDFs Representativos

Cargar los 3 documentos seleccionados de diferentes categorías.

In [22]:
# Definir rutas de los 3 PDFs representativos
pdf_paths = {
    "clinical": project_root / "data/pdf_papers/Enfoques Clínicos y Sistemas de Salud/Clinical Pathway for Suicide Risk Screening in Adult Primary Care Settings Special Recommendations.pdf",
    "ethics": project_root / "data/pdf_papers/Fundamentos Éticos y Gobernanza de Datos/ETHICS AND GOVERNANCE OF ARTIFICIAL INTELLIGENCE FOR HEALTH.pdf",
    "public_health": project_root / "data/pdf_papers/Perspectivas Salud Pública y Comunitaria/Effectiveness of suicide prevention interventions A systematic review and meta analysis.pdf"
}

# Verificar que los archivos existen
print("📂 Verificando archivos PDF...\n")
for category, path in pdf_paths.items():
    exists = "✅" if path.exists() else "❌"
    print(f"{exists} {category}: {path.name}")
    if not path.exists():
        print(f"   ⚠️  Archivo no encontrado: {path}")

📂 Verificando archivos PDF...

✅ clinical: Clinical Pathway for Suicide Risk Screening in Adult Primary Care Settings Special Recommendations.pdf
✅ ethics: ETHICS AND GOVERNANCE OF ARTIFICIAL INTELLIGENCE FOR HEALTH.pdf
✅ public_health: Effectiveness of suicide prevention interventions A systematic review and meta analysis.pdf


In [23]:
# Función para extraer texto de PDF con metadata
def extract_text_from_pdf(pdf_path, category):
    """
    Extrae texto de un PDF y retorna el contenido con metadata.
    """
    try:
        reader = PdfReader(pdf_path)
        
        # Metadata del PDF
        metadata = {
            "filename": pdf_path.name,
            "category": category,
            "num_pages": len(reader.pages),
            "extracted_at": datetime.now().isoformat()
        }
        
        # Extraer texto de todas las páginas
        full_text = ""
        for page_num, page in enumerate(reader.pages, start=1):
            text = page.extract_text()
            if text:
                full_text += f"\n--- Página {page_num} ---\n{text}"
        
        metadata["text_length"] = len(full_text)
        
        return full_text, metadata
        
    except Exception as e:
        print(f"❌ Error al procesar {pdf_path.name}: {e}")
        return None, None

# Extraer texto de los 3 PDFs
print("\n📄 Extrayendo texto de los PDFs...\n")

documents = {}
for category, path in pdf_paths.items():
    if path.exists():
        text, metadata = extract_text_from_pdf(path, category)
        if text:
            documents[category] = {
                "text": text,
                "metadata": metadata
            }
            print(f"✅ {category}:")
            print(f"   📄 Páginas: {metadata['num_pages']}")
            print(f"   📝 Caracteres: {metadata['text_length']:,}")
            print()

print(f"\n✅ Total de documentos cargados: {len(documents)}")


📄 Extrayendo texto de los PDFs...

✅ clinical:
   📄 Páginas: 14
   📝 Caracteres: 53,548

✅ ethics:
   📄 Páginas: 165
   📝 Caracteres: 492,884

✅ public_health:
   📄 Páginas: 14
   📝 Caracteres: 75,273


✅ Total de documentos cargados: 3


---
## 4️⃣ Análisis de Texto y Estructura

Analizar el contenido extraído para entender su estructura.

In [24]:
# Función para contar tokens (importante para costos y límites)
def count_tokens(text, model="gpt-4o-mini"):
    """
    Cuenta tokens usando tiktoken para estimar costos.
    """
    encoding = tiktoken.encoding_for_model(model)
    return len(encoding.encode(text))

# Análisis de cada documento
print("📊 ANÁLISIS DE DOCUMENTOS\n")
print("="*70)

total_tokens = 0
for category, doc_data in documents.items():
    text = doc_data["text"]
    metadata = doc_data["metadata"]
    
    tokens = count_tokens(text)
    total_tokens += tokens
    
    # Preview del texto
    preview = text[:300].replace("\n", " ").strip()
    
    print(f"\n📁 {category.upper()}")
    print(f"   Archivo: {metadata['filename']}")
    print(f"   Páginas: {metadata['num_pages']}")
    print(f"   Caracteres: {metadata['text_length']:,}")
    print(f"   Tokens: {tokens:,}")
    print(f"   Preview: {preview}...")
    print("-"*70)

print(f"\n🎯 TOTALES:")
print(f"   Total de tokens: {total_tokens:,}")
print(f"   Costo estimado embeddings (text-embedding-3-small): ${(total_tokens/1000000)*0.02:.4f}")
print(f"   Costo estimado consultas (50 consultas con gpt-4o-mini): ~$0.05")

📊 ANÁLISIS DE DOCUMENTOS


📁 CLINICAL
   Archivo: Clinical Pathway for Suicide Risk Screening in Adult Primary Care Settings Special Recommendations.pdf
   Páginas: 14
   Caracteres: 53,548
   Tokens: 12,171
   Preview: --- Página 1 --- Special Article Clinical Pathway for Suicide Risk Screening in Adult Primary Care Settings: Special Recommendations Lynsay Ayer, Ph.D., Lisa M. Horowitz, Ph.D., Lisa Colpe, Ph.D., Nathan J. Lowry, B.S., Patrick C. Ryan, B.S., Edwin Boudreaux, Ph.D., Virna Little, Psy.D., Stephen Er...
----------------------------------------------------------------------

📁 ETHICS
   Archivo: ETHICS AND GOVERNANCE OF ARTIFICIAL INTELLIGENCE FOR HEALTH.pdf
   Páginas: 165
   Caracteres: 492,884
   Tokens: 102,235
   Preview: --- Página 1 --- ETHICS AND GOVERNANCE OF ARTIFICIAL INTELLIGENCE FOR HEALTH 1 WHO GUIDANCE ETHICS AND GOVERNANCE OF ARTIFICIAL INTELLIGENCE FOR HEALTH --- Página 2 --- ETHICS AND GOVERNANCE OF ARTIFICIAL INTELLIGENCE FOR HEALTH 2 Ethics and governan

---
## 5️⃣ Estrategia de Chunking

Dividir los documentos en fragmentos (chunks) óptimos para el RAG.

**Estrategia elegida:** 
- Chunk size: 1000 caracteres
- Overlap: 200 caracteres
- Separadores: Respetando párrafos y secciones

In [25]:
# Configurar el text splitter
text_splitter = RecursiveCharacterTextSplitter(
    chunk_size=1000,
    chunk_overlap=200,
    length_function=len,
    separators=["\n\n", "\n", ". ", " ", ""]
)

print("⚙️ Configuración del Chunking:")
print(f"   Tamaño del chunk: 1000 caracteres")
print(f"   Overlap: 200 caracteres")
print(f"   Separadores: Párrafos, líneas, puntos, espacios\n")

# Crear chunks de los documentos
all_chunks = []

for category, doc_data in documents.items():
    text = doc_data["text"]
    metadata = doc_data["metadata"]
    
    # Crear chunks
    chunks = text_splitter.split_text(text)
    
    # Crear Document objects con metadata
    for i, chunk in enumerate(chunks):
        doc = Document(
            page_content=chunk,
            metadata={
                "source": metadata["filename"],
                "category": category,
                "chunk_id": i,
                "total_chunks": len(chunks)
            }
        )
        all_chunks.append(doc)
    
    print(f"✅ {category}: {len(chunks)} chunks creados")

print(f"\n🎯 Total de chunks: {len(all_chunks)}")

⚙️ Configuración del Chunking:
   Tamaño del chunk: 1000 caracteres
   Overlap: 200 caracteres
   Separadores: Párrafos, líneas, puntos, espacios

✅ clinical: 67 chunks creados
✅ ethics: 622 chunks creados
✅ public_health: 93 chunks creados

🎯 Total de chunks: 782


In [26]:
# Inspeccionar algunos chunks de ejemplo
print("\n📋 EJEMPLOS DE CHUNKS\n")
print("="*70)

# Mostrar 1 chunk de cada categoría
categories_shown = set()

for doc in all_chunks:
    category = doc.metadata["category"]
    if category not in categories_shown:
        print(f"\n📁 Categoría: {category}")
        print(f"   Fuente: {doc.metadata['source']}")
        print(f"   Chunk {doc.metadata['chunk_id'] + 1} de {doc.metadata['total_chunks']}")
        print(f"   Longitud: {len(doc.page_content)} caracteres")
        print(f"\n   Contenido:")
        preview = doc.page_content[:400].replace("\n", " ").strip()
        print(f"   {preview}...")
        print("-"*70)
        
        categories_shown.add(category)
        
        if len(categories_shown) >= 3:
            break


📋 EJEMPLOS DE CHUNKS


📁 Categoría: clinical
   Fuente: Clinical Pathway for Suicide Risk Screening in Adult Primary Care Settings Special Recommendations.pdf
   Chunk 1 de 67
   Longitud: 963 caracteres

   Contenido:
   --- Página 1 --- Special Article Clinical Pathway for Suicide Risk Screening in Adult Primary Care Settings: Special Recommendations Lynsay Ayer, Ph.D., Lisa M. Horowitz, Ph.D., Lisa Colpe, Ph.D., Nathan J. Lowry, B.S., Patrick C. Ryan, B.S., Edwin Boudreaux, Ph.D., Virna Little, Psy.D., Stephen Erban, M.D., Soett Ramirez-Estrada, M.D., Michael Schoenbaum, Ph.D. Suicide is a serious public health...
----------------------------------------------------------------------

📁 Categoría: ethics
   Fuente: ETHICS AND GOVERNANCE OF ARTIFICIAL INTELLIGENCE FOR HEALTH.pdf
   Chunk 1 de 622
   Longitud: 962 caracteres

   Contenido:
   --- Página 1 --- ETHICS AND GOVERNANCE OF ARTIFICIAL INTELLIGENCE FOR HEALTH 1 WHO GUIDANCE ETHICS AND GOVERNANCE OF ARTIFICIAL INTELLIGENCE FO

---
## 6️⃣ Creación de Embeddings y Vector Store

Generar embeddings con OpenAI y crear la base de datos vectorial con ChromaDB.

In [27]:
# Configurar embeddings de OpenAI
embeddings = OpenAIEmbeddings(
    model="text-embedding-3-small",
    openai_api_key=os.getenv('OPENAI_API_KEY')
)

print("✅ Embeddings configurados: text-embedding-3-small")
print("   📊 Dimensiones: 1536")
print("   💰 Costo: $0.02 por 1M tokens")

✅ Embeddings configurados: text-embedding-3-small
   📊 Dimensiones: 1536
   💰 Costo: $0.02 por 1M tokens


In [28]:
# Crear directorio para ChromaDB
chroma_dir = project_root / "data/chroma_db/exploration"
chroma_dir.mkdir(parents=True, exist_ok=True)

print(f"📁 Directorio ChromaDB: {chroma_dir}\n")

# Crear vector store
print("🔄 Creando vector store...")
print(f"   Procesando {len(all_chunks)} chunks...")
print("   Esto puede tomar 1-2 minutos...\n")

try:
    vectorstore = Chroma.from_documents(
        documents=all_chunks,
        embedding=embeddings,
        persist_directory=str(chroma_dir),
        collection_name="cuidar_rag_exploration"
    )
    
    print("✅ Vector store creado exitosamente!")
    print(f"   📊 Colección: cuidar_rag_exploration")
    print(f"   📦 Documentos indexados: {len(all_chunks)}")
    print(f"   💾 Almacenado en: {chroma_dir}")
    
except Exception as e:
    print(f"❌ Error al crear vector store: {e}")

📁 Directorio ChromaDB: /Users/reinerfuentesferrada/ONLINE_DS_THEBRIDGE_Rei/Proyecto ML/cuidar-ia/data/chroma_db/exploration

🔄 Creando vector store...
   Procesando 782 chunks...
   Esto puede tomar 1-2 minutos...

✅ Vector store creado exitosamente!
   📊 Colección: cuidar_rag_exploration
   📦 Documentos indexados: 782
   💾 Almacenado en: /Users/reinerfuentesferrada/ONLINE_DS_THEBRIDGE_Rei/Proyecto ML/cuidar-ia/data/chroma_db/exploration


---
## 7️⃣ Consultas de Prueba en Español

Probar el sistema RAG con consultas relacionadas con el CUIDAR Index.

In [29]:
# Configurar el retriever
retriever = vectorstore.as_retriever(
    search_type="similarity",
    search_kwargs={"k": 3}  # Retornar los 3 chunks más relevantes
)

print("✅ Retriever configurado")
print("   🔍 Tipo de búsqueda: Similarity")
print("   📊 Top K resultados: 3")

✅ Retriever configurado
   🔍 Tipo de búsqueda: Similarity
   📊 Top K resultados: 3


In [30]:
# Definir consultas de prueba relacionadas con CUIDAR Index
test_queries = [
    "¿Qué consideraciones éticas debo tener para manejar datos de predicción del suicidio?",
    "¿Cómo puedo mejorar la calidad de los datos para prevención del suicidio?",
    "Dame ejemplos de usos que se le pueden dar a los datos para tomar decisiones sobre prevención del suicidio",
    "¿Qué protocolos de screening o detección se recomiendan en atención primaria?"
]

print("📋 Consultas de prueba definidas:")
for i, query in enumerate(test_queries, 1):
    print(f"   {i}. {query}")

📋 Consultas de prueba definidas:
   1. ¿Qué consideraciones éticas debo tener para manejar datos de predicción del suicidio?
   2. ¿Cómo puedo mejorar la calidad de los datos para prevención del suicidio?
   3. Dame ejemplos de usos que se le pueden dar a los datos para tomar decisiones sobre prevención del suicidio
   4. ¿Qué protocolos de screening o detección se recomiendan en atención primaria?


In [31]:
# Función para realizar búsqueda y mostrar resultados
def search_and_display(query, retriever, show_full_content=False):
    """
    Realiza búsqueda semántica y muestra resultados formateados.
    """
    print("\n" + "="*70)
    print(f"🔍 CONSULTA: {query}")
    print("="*70)
    
    # Realizar búsqueda
    results = retriever.get_relevant_documents(query)
    
    if not results:
        print("❌ No se encontraron resultados relevantes")
        return
    
    print(f"\n📊 Se encontraron {len(results)} resultados relevantes\n")
    
    # Mostrar cada resultado
    for i, doc in enumerate(results, 1):
        print(f"\n📄 Resultado {i}:")
        print(f"   Fuente: {doc.metadata['source']}")
        print(f"   Categoría: {doc.metadata['category']}")
        print(f"   Chunk: {doc.metadata['chunk_id'] + 1}/{doc.metadata['total_chunks']}")
        print(f"   Longitud: {len(doc.page_content)} caracteres")
        
        if show_full_content:
            print(f"\n   Contenido completo:")
            print(f"   {doc.page_content}")
        else:
            print(f"\n   Preview:")
            preview = doc.page_content[:300].replace("\n", " ").strip()
            print(f"   {preview}...")
        
        print("-"*70)
    
    return results

In [34]:
# Función CORREGIDA para realizar búsqueda y mostrar resultados
def search_and_display(query, retriever, show_full_content=False):
    """
    Realiza búsqueda semántica y muestra resultados formateados.
    """
    print("\n" + "="*70)
    print(f"🔍 CONSULTA: {query}")
    print("="*70)
    
    # Realizar búsqueda (método actualizado para LangChain 1.0+)
    results = retriever.invoke(query)
    
    if not results:
        print("❌ No se encontraron resultados relevantes")
        return
    
    print(f"\n📊 Se encontraron {len(results)} resultados relevantes\n")
    
    # Mostrar cada resultado
    for i, doc in enumerate(results, 1):
        print(f"\n📄 Resultado {i}:")
        print(f"   Fuente: {doc.metadata['source']}")
        print(f"   Categoría: {doc.metadata['category']}")
        print(f"   Chunk: {doc.metadata['chunk_id'] + 1}/{doc.metadata['total_chunks']}")
        print(f"   Longitud: {len(doc.page_content)} caracteres")
        
        if show_full_content:
            print(f"\n   Contenido completo:")
            print(f"   {doc.page_content}")
        else:
            print(f"\n   Preview:")
            preview = doc.page_content[:300].replace("\n", " ").strip()
            print(f"   {preview}...")
        
        print("-"*70)
    
    return results

In [35]:
# Probar la primera consulta con detalle
results_1 = search_and_display(
    test_queries[0],
    retriever,
    show_full_content=False  # Cambiar a True para ver contenido completo
)


🔍 CONSULTA: ¿Qué consideraciones éticas debo tener para manejar datos de predicción del suicidio?

📊 Se encontraron 3 resultados relevantes


📄 Resultado 1:
   Fuente: Clinical Pathway for Suicide Risk Screening in Adult Primary Care Settings Special Recommendations.pdf
   Categoría: clinical
   Chunk: 30/67
   Longitud: 988 caracteres

   Preview:
   22. Ahmedani BK, Simon GE, Stewart C, et al: Health care contacts in the year before suicide death. J Gen Intern Med 2014; 29:870–877 23. Chiang A, Paynter J, Edlin R, Exeter DJ: Suicide preceded by health services contact - a whole-of-population study in New Zealand 2013-2015. PLoS One 2021; 16:e02...
----------------------------------------------------------------------

📄 Resultado 2:
   Fuente: Clinical Pathway for Suicide Risk Screening in Adult Primary Care Settings Special Recommendations.pdf
   Categoría: clinical
   Chunk: 30/67
   Longitud: 988 caracteres

   Preview:
   22. Ahmedani BK, Simon GE, Stewart C, et al: Health care 

In [36]:
# Probar la segunda consulta
results_2 = search_and_display(
    test_queries[1],
    retriever,
    show_full_content=False
)


🔍 CONSULTA: ¿Cómo puedo mejorar la calidad de los datos para prevención del suicidio?

📊 Se encontraron 3 resultados relevantes


📄 Resultado 1:
   Fuente: Clinical Pathway for Suicide Risk Screening in Adult Primary Care Settings Special Recommendations.pdf
   Categoría: clinical
   Chunk: 30/67
   Longitud: 988 caracteres

   Preview:
   22. Ahmedani BK, Simon GE, Stewart C, et al: Health care contacts in the year before suicide death. J Gen Intern Med 2014; 29:870–877 23. Chiang A, Paynter J, Edlin R, Exeter DJ: Suicide preceded by health services contact - a whole-of-population study in New Zealand 2013-2015. PLoS One 2021; 16:e02...
----------------------------------------------------------------------

📄 Resultado 2:
   Fuente: Clinical Pathway for Suicide Risk Screening in Adult Primary Care Settings Special Recommendations.pdf
   Categoría: clinical
   Chunk: 30/67
   Longitud: 988 caracteres

   Preview:
   22. Ahmedani BK, Simon GE, Stewart C, et al: Health care contacts in 

In [37]:
# Probar la tercera consulta
results_3 = search_and_display(
    test_queries[2],
    retriever,
    show_full_content=False
)


🔍 CONSULTA: Dame ejemplos de usos que se le pueden dar a los datos para tomar decisiones sobre prevención del suicidio

📊 Se encontraron 3 resultados relevantes


📄 Resultado 1:
   Fuente: Clinical Pathway for Suicide Risk Screening in Adult Primary Care Settings Special Recommendations.pdf
   Categoría: clinical
   Chunk: 30/67
   Longitud: 988 caracteres

   Preview:
   22. Ahmedani BK, Simon GE, Stewart C, et al: Health care contacts in the year before suicide death. J Gen Intern Med 2014; 29:870–877 23. Chiang A, Paynter J, Edlin R, Exeter DJ: Suicide preceded by health services contact - a whole-of-population study in New Zealand 2013-2015. PLoS One 2021; 16:e02...
----------------------------------------------------------------------

📄 Resultado 2:
   Fuente: Clinical Pathway for Suicide Risk Screening in Adult Primary Care Settings Special Recommendations.pdf
   Categoría: clinical
   Chunk: 30/67
   Longitud: 988 caracteres

   Preview:
   22. Ahmedani BK, Simon GE, Stewart C

In [38]:
# Probar la cuarta consulta
results_4 = search_and_display(
    test_queries[3],
    retriever,
    show_full_content=False
)


🔍 CONSULTA: ¿Qué protocolos de screening o detección se recomiendan en atención primaria?

📊 Se encontraron 3 resultados relevantes


📄 Resultado 1:
   Fuente: Clinical Pathway for Suicide Risk Screening in Adult Primary Care Settings Special Recommendations.pdf
   Categoría: clinical
   Chunk: 8/67
   Longitud: 958 caracteres

   Preview:
   developed a quality-improvement program to universally screen patients. They found that 3.9% of patients overall screened positive, across all their care settings, including screener positive rates of 6.3% among emergency department patients and 2.1% among patients in outpa- tient clinics. 11 Simila...
----------------------------------------------------------------------

📄 Resultado 2:
   Fuente: Clinical Pathway for Suicide Risk Screening in Adult Primary Care Settings Special Recommendations.pdf
   Categoría: clinical
   Chunk: 8/67
   Longitud: 958 caracteres

   Preview:
   developed a quality-improvement program to universally screen patie

---
## 8️⃣ Evaluación de Calidad del RAG

Analizar la relevancia y calidad de los resultados obtenidos.

In [39]:
# Análisis de diversidad de fuentes
print("📊 ANÁLISIS DE RESULTADOS\n")
print("="*70)

all_test_results = [results_1, results_2, results_3, results_4]

for i, (query, results) in enumerate(zip(test_queries, all_test_results), 1):
    if results:
        categories = [doc.metadata['category'] for doc in results]
        sources = [doc.metadata['source'] for doc in results]
        
        print(f"\nConsulta {i}:")
        print(f"   Pregunta: {query[:60]}...")
        print(f"   Categorías encontradas: {set(categories)}")
        print(f"   Diversidad de fuentes: {len(set(sources))} documentos diferentes")
        print("-"*70)

print("\n✅ Análisis completado")

📊 ANÁLISIS DE RESULTADOS


Consulta 1:
   Pregunta: ¿Qué consideraciones éticas debo tener para manejar datos de...
   Categorías encontradas: {'clinical', 'ethics'}
   Diversidad de fuentes: 2 documentos diferentes
----------------------------------------------------------------------

Consulta 2:
   Pregunta: ¿Cómo puedo mejorar la calidad de los datos para prevención ...
   Categorías encontradas: {'clinical', 'public_health'}
   Diversidad de fuentes: 2 documentos diferentes
----------------------------------------------------------------------

Consulta 3:
   Pregunta: Dame ejemplos de usos que se le pueden dar a los datos para ...
   Categorías encontradas: {'clinical', 'public_health'}
   Diversidad de fuentes: 2 documentos diferentes
----------------------------------------------------------------------

Consulta 4:
   Pregunta: ¿Qué protocolos de screening o detección se recomiendan en a...
   Categorías encontradas: {'clinical'}
   Diversidad de fuentes: 1 documentos diferent

In [40]:
# Guardar resumen de la exploración
summary = {
    "fecha_exploracion": datetime.now().isoformat(),
    "documentos_procesados": len(documents),
    "chunks_creados": len(all_chunks),
    "total_tokens": total_tokens,
    "consultas_realizadas": len(test_queries),
    "configuracion": {
        "chunk_size": 1000,
        "chunk_overlap": 200,
        "embedding_model": "text-embedding-3-small",
        "vector_store": "ChromaDB"
    },
    "categorias": list(documents.keys())
}

summary_path = project_root / "data/rag_exploration_summary.json"
with open(summary_path, 'w', encoding='utf-8') as f:
    json.dump(summary, f, indent=2, ensure_ascii=False)

print(f"✅ Resumen guardado en: {summary_path}")
print("\n📊 Resumen de la exploración:")
print(json.dumps(summary, indent=2, ensure_ascii=False))

✅ Resumen guardado en: /Users/reinerfuentesferrada/ONLINE_DS_THEBRIDGE_Rei/Proyecto ML/cuidar-ia/data/rag_exploration_summary.json

📊 Resumen de la exploración:
{
  "fecha_exploracion": "2025-11-18T09:43:50.466471",
  "documentos_procesados": 3,
  "chunks_creados": 782,
  "total_tokens": 133873,
  "consultas_realizadas": 4,
  "configuracion": {
    "chunk_size": 1000,
    "chunk_overlap": 200,
    "embedding_model": "text-embedding-3-small",
    "vector_store": "ChromaDB"
  },
  "categorias": [
    "clinical",
    "ethics",
    "public_health"
  ]
}


In [41]:
# Defino el prompt del sistema para el asistente RAG
# Este prompt establece el rol y las instrucciones para generar respuestas

SYSTEM_PROMPT = """
Eres un asistente experto en prevención del suicidio, gobernanza de datos y políticas públicas de salud mental.

Tu rol es apoyar a equipos de gobiernos locales y servicios de salud en la toma de decisiones basadas en evidencia para la prevención del suicidio.

Instrucciones:
1. Responde siempre en español, de forma clara y profesional.
2. Basa tus respuestas en el contexto proporcionado (documentos científicos y guías).
3. Cita las fuentes cuando sea relevante (nombre del documento).
4. Si la información del contexto es insuficiente, indícalo claramente.
5. Cuando sea pertinente, sugiere que el usuario considere investigación o datos locales para complementar las recomendaciones.
6. Mantén un tono técnico pero accesible para tomadores de decisiones.
7. Prioriza recomendaciones prácticas y accionables.

Recuerda: Tu objetivo es facilitar el uso efectivo de datos para la prevención del suicidio, alineado con las dimensiones del índice CUIDAR (Accesibilidad, Calidad, Interoperabilidad, Uso, Capacidad Analítica, Gestión del Conocimiento, Ética y Gobernanza).
"""

print("Prompt del sistema configurado")
print(f"Longitud: {len(SYSTEM_PROMPT)} caracteres")

Prompt del sistema configurado
Longitud: 1073 caracteres


In [42]:
def generate_rag_response(query, retriever, client, k=3, show_sources=True):
    """
    Genera una respuesta utilizando RAG (Retrieval-Augmented Generation).
    
    Parámetros:
    - query: Pregunta del usuario en español
    - retriever: Objeto retriever de LangChain
    - client: Cliente de OpenAI
    - k: Número de chunks a recuperar
    - show_sources: Si se muestran las fuentes utilizadas
    
    Retorna:
    - Diccionario con la respuesta, fuentes y metadatos
    """
    
    # Paso 1: Recuperar chunks relevantes
    retrieved_docs = retriever.invoke(query)
    
    if not retrieved_docs:
        return {
            "respuesta": "No encontré información relevante en la base de conocimiento para responder esta consulta.",
            "fuentes": [],
            "chunks_utilizados": 0
        }
    
    # Paso 2: Construir el contexto a partir de los chunks
    context_parts = []
    sources = []
    
    for i, doc in enumerate(retrieved_docs, 1):
        source_name = doc.metadata.get('source', 'Fuente desconocida')
        category = doc.metadata.get('category', 'Sin categoría')
        
        context_parts.append(f"[Documento {i} - {source_name}]:\n{doc.page_content}")
        
        if source_name not in sources:
            sources.append(source_name)
    
    context = "\n\n".join(context_parts)
    
    # Paso 3: Construir el prompt para el usuario
    user_prompt = f"""Contexto (documentos recuperados de la base de conocimiento):

{context}

---

Pregunta del usuario:
{query}

Por favor, responde basándote en el contexto proporcionado. Si consideras que sería útil contar con datos o investigación local para complementar la respuesta, menciónalo."""
    
    # Paso 4: Generar respuesta con GPT-4o-mini
    try:
        response = client.chat.completions.create(
            model="gpt-4o-mini",
            messages=[
                {"role": "system", "content": SYSTEM_PROMPT},
                {"role": "user", "content": user_prompt}
            ],
            temperature=0.3,
            max_tokens=1000
        )
        
        answer = response.choices[0].message.content
        tokens_used = response.usage.total_tokens
        
    except Exception as e:
        return {
            "respuesta": f"Error al generar respuesta: {str(e)}",
            "fuentes": sources,
            "chunks_utilizados": len(retrieved_docs)
        }
    
    return {
        "respuesta": answer,
        "fuentes": sources,
        "chunks_utilizados": len(retrieved_docs),
        "tokens_utilizados": tokens_used
    }

print("Función generate_rag_response definida correctamente")

Función generate_rag_response definida correctamente


In [43]:
def display_rag_response(query, result):
    """
    Muestra la respuesta RAG de forma formateada.
    """
    print("="*70)
    print(f"CONSULTA: {query}")
    print("="*70)
    print("\nRESPUESTA:\n")
    print(result["respuesta"])
    print("\n" + "-"*70)
    print("\nFUENTES UTILIZADAS:")
    for i, source in enumerate(result["fuentes"], 1):
        print(f"  {i}. {source}")
    print(f"\nChunks recuperados: {result['chunks_utilizados']}")
    if "tokens_utilizados" in result:
        print(f"Tokens utilizados: {result['tokens_utilizados']}")
    print("="*70)

print("Función display_rag_response definida correctamente")

Función display_rag_response definida correctamente


### 9.1 Pruebas del Sistema RAG Completo

Ejecuto las consultas de prueba para validar que el sistema genera respuestas coherentes y útiles en español.

In [44]:
# Primera consulta: Consideraciones éticas
query_1 = "¿Qué consideraciones éticas debo tener para manejar datos de predicción del suicidio?"

result_1 = generate_rag_response(query_1, retriever, client)
display_rag_response(query_1, result_1)

CONSULTA: ¿Qué consideraciones éticas debo tener para manejar datos de predicción del suicidio?

RESPUESTA:

Al manejar datos de predicción del suicidio, es fundamental considerar varios aspectos éticos que aseguren la protección de la privacidad y los derechos de los individuos. A continuación, se presentan algunas consideraciones clave:

1. **Consentimiento Informado**: Es esencial obtener el consentimiento informado de las personas antes de utilizar sus datos para predicciones relacionadas con el suicidio. Esto implica que los individuos deben ser plenamente conscientes de cómo se utilizarán sus datos y los posibles riesgos asociados (Documento 3).

2. **Autonomía del Paciente**: Respetar la autonomía de los individuos es crucial. Las predicciones sobre su salud mental deben ser manejadas con sensibilidad, evitando cualquier forma de coerción o presión para participar en estudios o intervenciones basadas en esos datos (Documento 3).

3. **Minimización de Sesgos**: Al utilizar modelo

In [45]:
# Segunda consulta: Calidad de datos
query_2 = "¿Cómo puedo mejorar la calidad de los datos para prevención del suicidio?"

result_2 = generate_rag_response(query_2, retriever, client)
display_rag_response(query_2, result_2)

CONSULTA: ¿Cómo puedo mejorar la calidad de los datos para prevención del suicidio?

RESPUESTA:

Mejorar la calidad de los datos para la prevención del suicidio es fundamental para desarrollar políticas efectivas y basadas en evidencia. A continuación, se presentan algunas recomendaciones prácticas y accionables:

1. **Establecer Protocolos de Recolección de Datos**: Implementar protocolos estandarizados para la recolección de datos sobre intentos de suicidio y suicidios consumados. Esto incluye información sobre antecedentes médicos, contactos previos con servicios de salud y factores de riesgo identificados. La investigación de Ahmedani et al. (2014) destaca la importancia de los contactos con servicios de salud antes de un suicidio, lo que sugiere que estos datos son cruciales para entender el contexto (Ahmedani BK, Simon GE, Stewart C, et al.).

2. **Capacitación del Personal**: Capacitar a los profesionales de la salud en la identificación y registro de factores de riesgo asociado

In [46]:
# Tercera consulta: Ejemplos de uso de datos
query_3 = "Dame ejemplos de usos que se le pueden dar a los datos para tomar decisiones sobre prevención del suicidio"

result_3 = generate_rag_response(query_3, retriever, client)
display_rag_response(query_3, result_3)

CONSULTA: Dame ejemplos de usos que se le pueden dar a los datos para tomar decisiones sobre prevención del suicidio

RESPUESTA:

Los datos son fundamentales para la toma de decisiones informadas en la prevención del suicidio. A continuación, se presentan algunos ejemplos de cómo se pueden utilizar estos datos:

1. **Identificación de Grupos de Riesgo**: Utilizando datos sobre contactos previos con servicios de salud, como se menciona en el estudio de Ahmedani et al. (2014), se pueden identificar grupos de población que tienen un mayor riesgo de suicidio. Esto permite a los servicios de salud enfocar sus esfuerzos en la atención de estas poblaciones específicas.

2. **Evaluación de la Efectividad de Intervenciones**: Los datos sobre la efectividad de programas de prevención, como los analizados en la revisión sistemática y meta-análisis (Documento 3), pueden ayudar a determinar qué intervenciones son más efectivas en diferentes contextos. Esto incluye la implementación de programas de 

In [47]:
# Cuarta consulta: Protocolos de screening
query_4 = "¿Qué protocolos de screening o detección se recomiendan en atención primaria?"

result_4 = generate_rag_response(query_4, retriever, client)
display_rag_response(query_4, result_4)

CONSULTA: ¿Qué protocolos de screening o detección se recomiendan en atención primaria?

RESPUESTA:

En el contexto de la atención primaria, se recomienda implementar protocolos de screening universal para la detección del riesgo de suicidio. Según los documentos revisados, se ha observado que aproximadamente el 3.9% de los pacientes en diversos entornos de atención médica presentan resultados positivos en las pruebas de detección de riesgo suicida. Específicamente, las tasas de resultados positivos son más altas en departamentos de emergencia (6.3%) en comparación con clínicas ambulatorias (2.1%) (Documento 1).

### Recomendaciones para el Screening en Atención Primaria:

1. **Implementación de Screening Universal**: Se sugiere que todos los pacientes sean sometidos a un screening para el riesgo de suicidio, independientemente de su presentación clínica. Esto es especialmente relevante en entornos donde los recursos pueden ser limitados (Documento 1).

2. **Frecuencia del Screening**:

### 9.2 Consulta Personalizada

Celda para realizar consultas adicionales al sistema RAG.

In [48]:
# Consulta personalizada - modificar según necesidad
mi_consulta = "¿Qué indicadores debo considerar para evaluar la interoperabilidad de sistemas de datos en salud mental?"

mi_resultado = generate_rag_response(mi_consulta, retriever, client)
display_rag_response(mi_consulta, mi_resultado)

CONSULTA: ¿Qué indicadores debo considerar para evaluar la interoperabilidad de sistemas de datos en salud mental?

RESPUESTA:

Para evaluar la interoperabilidad de sistemas de datos en salud mental, es fundamental considerar una serie de indicadores que aseguren que los sistemas puedan comunicarse y compartir información de manera efectiva y segura. Basándome en el contexto proporcionado, aquí hay algunos indicadores clave que podrías considerar:

1. **Cumplimiento de estándares internacionales**: Verificar si los sistemas de datos cumplen con estándares reconocidos, como los de la ISO (por ejemplo, ISO 27001 para la gestión de la seguridad de la información) y Health Level 7 (HL7) para la transferencia de datos clínicos. Esto asegura que los sistemas puedan interoperar con otras tecnologías de salud.

2. **Calidad de los datos**: Evaluar la representatividad, precisión y consistencia de los datos. Datos de alta calidad son esenciales para evitar inferencias sesgadas y análisis erróne

---
## 10. Conclusiones y Próximos Pasos

### Resultados de la Exploración

En este notebook validé el pipeline completo de RAG para CUIDAR IA:

1. **Configuración de OpenAI API**: Conexión exitosa con embeddings y modelo de chat.
2. **Procesamiento de documentos**: Carga y chunking de 3 documentos representativos.
3. **Vector store**: Creación exitosa de la base vectorial con ChromaDB.
4. **Búsqueda semántica**: El sistema recupera chunks relevantes a partir de consultas en español.
5. **Generación de respuestas**: GPT-4o-mini genera respuestas coherentes en español basadas en el contexto recuperado.

### Observaciones Técnicas

- Los embeddings multilingües de OpenAI manejan correctamente la búsqueda cross-lingual (español - inglés).
- El chunking de 1000 caracteres con overlap de 200 proporciona contexto suficiente.
- La temperatura de 0.3 genera respuestas consistentes y factuales.

### Próximos Pasos

1. **Escalar a colección completa**: Procesar los ~30 documentos de las 3 categorías.
2. **Optimizar retrieval**: Ajustar parámetros k y score_threshold según resultados.
3. **Modularizar código**: Crear módulos Python reutilizables en `src/rag/`.
4. **Integrar con CUIDAR Index**: Conectar las recomendaciones RAG con los resultados del índice de evaluación.
5. **Implementar caché**: Reducir costos almacenando respuestas frecuentes.

### Estimación de Costos para Producción

- Embeddings (30 documentos): ~$0.10 - $0.50 USD
- Consultas (100 consultas/mes): ~$0.50 - $1.00 USD
- **Total mensual estimado**: < $2.00 USD

In [49]:
# Actualizo el resumen con los resultados de generación
summary["generacion_respuestas"] = {
    "modelo": "gpt-4o-mini",
    "temperatura": 0.3,
    "max_tokens": 1000,
    "consultas_probadas": 4,
    "estado": "validado"
}

# Guardo el resumen actualizado
with open(summary_path, 'w', encoding='utf-8') as f:
    json.dump(summary, f, indent=2, ensure_ascii=False)

print(f"Resumen actualizado guardado en: {summary_path}")
print("\nResumen final:")
print(json.dumps(summary, indent=2, ensure_ascii=False))

Resumen actualizado guardado en: /Users/reinerfuentesferrada/ONLINE_DS_THEBRIDGE_Rei/Proyecto ML/cuidar-ia/data/rag_exploration_summary.json

Resumen final:
{
  "fecha_exploracion": "2025-11-18T09:43:50.466471",
  "documentos_procesados": 3,
  "chunks_creados": 782,
  "total_tokens": 133873,
  "consultas_realizadas": 4,
  "configuracion": {
    "chunk_size": 1000,
    "chunk_overlap": 200,
    "embedding_model": "text-embedding-3-small",
    "vector_store": "ChromaDB"
  },
  "categorias": [
    "clinical",
    "ethics",
    "public_health"
  ],
  "generacion_respuestas": {
    "modelo": "gpt-4o-mini",
    "temperatura": 0.3,
    "max_tokens": 1000,
    "consultas_probadas": 4,
    "estado": "validado"
  }
}


In [50]:
ls -la "/Users/reinerfuentesferrada/ONLINE_DS_THEBRIDGE_Rei/Proyecto ML/cuidar-ia/data/pdf_papers/"

total 32
drwxr-xr-x@  7 reinerfuentesferrada  staff    224 Nov 11 12:59 ./
drwxr-xr-x@  7 reinerfuentesferrada  staff    224 Nov 18 09:43 ../
-rw-r--r--@  1 reinerfuentesferrada  staff  14340 Nov 11 13:34 .DS_Store
-rw-r--r--@  1 reinerfuentesferrada  staff      0 Nov 10 10:54 .gitkeep
drwxr-xr-x  13 reinerfuentesferrada  staff    416 Nov 11 12:55 Enfoques Clínicos y Sistemas de Salud/
drwxr-xr-x  13 reinerfuentesferrada  staff    416 Nov 11 12:14 Fundamentos Éticos y Gobernanza de Datos/
drwxr-xr-x  12 reinerfuentesferrada  staff    384 Nov 11 13:24 Perspectivas Salud Pública y Comunitaria/


In [51]:
ls "/Users/reinerfuentesferrada/ONLINE_DS_THEBRIDGE_Rei/Proyecto ML/cuidar-ia/data/pdf_papers/Enfoques Clínicos y Sistemas de Salud/" | wc -l

      10


In [52]:
ls "/Users/reinerfuentesferrada/ONLINE_DS_THEBRIDGE_Rei/Proyecto ML/cuidar-ia/data/pdf_papers/Fundamentos Éticos y Gobernanza de Datos/" | wc -l

      10


In [53]:
ls "/Users/reinerfuentesferrada/ONLINE_DS_THEBRIDGE_Rei/Proyecto ML/cuidar-ia/data/pdf_papers/Fundamentos Éticos y Gobernanza de Datos/" | wc -l

      10


In [2]:
import os

def tree(dir_path, prefix=""):
    """Imprime la estructura de carpetas y archivos tipo árbol"""
    contents = os.listdir(dir_path)
    contents.sort()
    for i, item in enumerate(contents):
        path = os.path.join(dir_path, item)
        connector = "├── " if i < len(contents) - 1 else "└── "
        print(prefix + connector + item)
        if os.path.isdir(path):
            extension = "│   " if i < len(contents) - 1 else "    "
            tree(path, prefix + extension)

if __name__ == "__main__":
    # Cambia esta ruta por la ruta de tu proyecto
    project_path = r"/Users/reinerfuentesferrada/ONLINE_DS_THEBRIDGE_Rei/Proyecto ML/cuidar-ia"
    print(os.path.basename(project_path))
    tree(project_path)

cuidar-ia
├── .DS_Store
├── .env
├── .env.example
├── .gitignore
├── CONFIGURACION_API_KEYS.md
├── INICIO_RAPIDO.md
├── README.md
├── app
│   ├── .DS_Store
│   ├── main.py
│   ├── pages
│   │   ├── 1_Diagnostico_CUIDAR_Index.py
│   │   ├── 2_Consultar_CUIDAR_IA.py
│   │   ├── 3_Informacion_Territorio.py
│   │   └── 4_Resultados_CUIDAR_Index.py
│   └── utils
│       ├── __init__.py
│       ├── __pycache__
│       │   ├── __init__.cpython-312.pyc
│       │   ├── config.cpython-312.pyc
│       │   └── rag_engine.cpython-312.pyc
│       ├── config.py
│       └── rag_engine.py
├── cuidar_ia_fase3
│   ├── .env.example
│   ├── .gitignore
│   ├── LICENSE
│   ├── README.md
│   ├── config
│   │   ├── __init__.py
│   │   └── settings.py
│   ├── data
│   │   └── {uploads,anonymized}
│   ├── docs
│   │   ├── INSTALACION.md
│   │   └── ejemplos
│   ├── fase3_evaluator
│   │   ├── __init__.py
│   │   ├── agent
│   │   │   ├── __init__.py
│   │   │   ├── interpreter.py
│   │   │   └── prompts.py
│   │